# Context Managers
## For When You Need to Manage Contexts
### Most Common Use: Files

In [1]:
with open('./data/iris.csv') as data_file:
    top_line = data_file.readline()
    
print(top_line)

sepal_length,sepal_width,petal_length,petal_width,species



#### What It Does (0th Order Approximation)

In [2]:
try:
    data_file = open('./data/iris.csv')
    top_line = data_file.readline()
except:
    pass
finally:
    data_file.close()
    
print(top_line)

sepal_length,sepal_width,petal_length,petal_width,species



#### What It Does (1st Order Approximation)

In [3]:
class DemoFile:
    def __init__(self, filename):
        self.name = filename
        print('Inititializing {f}'.format(f=filename))
        
    def readline(self):
        return 'This is the first line of the file'
    
    def close(self):
        print('Closing the file')
        
    def __enter__(self):
        print('In the __enter__ method')
        return self
    
    def __exit__(self, type, value, traceback):
        print('Closing file')
        
def open_demo_file(name):
    return DemoFile(name)

with open_demo_file('demo') as my_file:
    first_line = my_file.readline()
    
print(first_line)

Inititializing demo
In the __enter__ method
Closing file
This is the first line of the file


#### What It Does (Words)

* The with statement stores the __\_\_exit\_\___ method of the File class.
* It calls the __\_\_enter\_\___ method of the File class.
* The __\_\_enter\_\___ method opens the file and returns it.
* The opened file handle is passed to opened_file.
* We write to the file using .write().
* The with statement calls the stored __\_\_exit\_\___ method.
* The __\_\_exit\_\___ method closes the file.


### Shared Resource Management
Moment of advertising: Upcoming PSG on multithreading!

In [4]:
import time
import threading

class Resource:
    def __init__(self):
        self.users = 0
    def __enter__(self):
        self.users += 1
    def __exit__(self, type, value, traceback):
        self.users -= 1
        
def thread_work(resource, name, iterations):
    print('{name}\'s thread is starting'.format(name=name))
    with resource:
        for i in range(iterations):
            print('{name}: My resource has {n} active users'.format(name=name, n=resource.users))
            time.sleep(1)
    print('{name} is done'.format(name=name))

my_resource = Resource()
x = threading.Thread(target=thread_work, args=(my_resource, 'Becca', 2))
y = threading.Thread(target=thread_work, args=(my_resource, 'Chris', 3))
z = threading.Thread(target=thread_work, args=(my_resource, 'Ned', 4))
x.start()
y.start()
z.start()
x.join()
y.join()
z.join()

print(my_resource.users)
        


Becca's thread is starting
Becca: My resource has 1 active users
Chris's thread is starting
Chris: My resource has 2 active users
Ned's thread is starting
Ned: My resource has 3 active users
Chris: My resource has 3 active usersBecca: My resource has 3 active users

Ned: My resource has 3 active users
Chris: My resource has 3 active usersBecca is done

Ned: My resource has 2 active users
Chris is done
Ned: My resource has 1 active users
Ned is done
0


### But Wait, There's Less!
#### Decorators III: Return of the Bride of Decorators

In [5]:
import time
import threading
from contextlib import contextmanager


class MiniResource:
    def __init__(self):
        self.users = 0
        
def thread_work(resource, name, iterations):
    print('{name}\'s thread is starting'.format(name=name))
    with get_resource(resource):
        for i in range(iterations):
            print('{name}: My resource has {n} active users'.format(name=name, n=resource.users))
            time.sleep(1)
    print('{name} is done'.format(name=name))
    
@contextmanager
def get_resource(resource):
    resource.users += 1
    yield resource
    resource.users -= 1
    
    

my_resource = MiniResource()
x = threading.Thread(target=thread_work, args=(my_resource, 'Becca', 2))
y = threading.Thread(target=thread_work, args=(my_resource, 'Chris', 3))
z = threading.Thread(target=thread_work, args=(my_resource, 'Ned', 4))
x.start()
y.start()
z.start()
x.join()
y.join()
z.join()

print(my_resource.users)

Becca's thread is startingChris's thread is starting
Becca: My resource has 1 active users

Chris: My resource has 2 active users
Ned's thread is starting
Ned: My resource has 3 active users
Becca: My resource has 3 active usersChris: My resource has 3 active users

Ned: My resource has 3 active users
Chris: My resource has 3 active users
Becca is done
Ned: My resource has 2 active users
Chris is doneNed: My resource has 1 active users

Ned is done
0


### Sometimes It Don't Go Your Way


In [6]:
with Resource() as resource:
    raise Exception('something has gone terribly wrong')

Exception: something has gone terribly wrong

In [7]:
class ResourceWithExceptionHandling:
    def __init__(self):
        self.users = 0
    def __enter__(self):
        self.users += 1
    def __exit__(self, type, value, traceback):
        if value:
            print('An exception was raised: {v}'.format(v=value))
        self.users -= 1
        return True
    
with ResourceWithExceptionHandling() as new_resource:
    raise Exception('something has gone terribly wrong')

An exception was raised: something has gone terribly wrong
